In [1]:
# Copyright 2025 Keysight Technologies Inc.

In [2]:
import keysight.qcs as qcs

# create a topology consisting of 4 qudits with couplings between (0, 2) and (1, 3)
n_qudits = 4
qudits = qcs.Qudits(range(n_qudits))
pairs = qudits.make_connectivity([(0, 2), (1, 3)])

# instantiate a qudit graph with the above couplings
topology = qcs.QuditGraph(qudits, pairs)

# instantiate a new calibration set with this topology
calset = qcs.CalibrationSet(topology)

In [3]:
qudit_frequencies = qcs.Array(
    "qudit_freqs", value=[4.91e9, 4.92e9, 4.93e9, 4.94e9], dtype=float
)
readout_frequencies = qcs.Array(
    "readout_freqs", value=[5.91e9, 5.92e9, 5.93e9, 5.94e9], dtype=float
)

durations = qcs.Array("multi_qubit_duration", value=[50e-9, 60e-9], dtype=float)
amplitudes = qcs.Array("multi_qubit_amplitudes", value=[0.5, 0.6], dtype=float)


# define virtual channels to represent our qudit channels
channels = qcs.Channels(range(n_qudits), "control")
readout_channels = qcs.Channels(range(n_qudits), "readout")

In [4]:
# define the matching waveform for an X gate
x_waveform = qcs.RFWaveform(50e-9, qcs.GaussianEnvelope(), 0.5, qudit_frequencies)

# add to calibration set
calset.add_sq_gate("x", qcs.GATES.x, x_waveform, channels=channels)

In [5]:
calset.variable_list

[Array(name=x_duration, shape=(4,), dtype=float, unit=s),
 Array(name=x_amplitude, shape=(4,), dtype=float, unit=none),
 Array(name=qudit_freqs, shape=(4,), dtype=float, unit=Hz),
 Array(name=x_phase, shape=(4,), dtype=float, unit=rad),
 Array(name=x_post_phase, shape=(4,), dtype=float, unit=rad)]

In [6]:
calset.variables.x_duration.value

array([5.e-08, 5.e-08, 5.e-08, 5.e-08])

In [7]:
# calset.export_values("calibration_values.qcs")

loaded_file = open("calibration_values.qcs").read()
print(loaded_file)

{
  "qudits_0": {
    "x_duration": 5E-08,
    "x_amplitude": 0.5,
    "qudit_freqs": 4910000000.0,
    "x_phase": 0.0,
    "x_post_phase": 0.0
  },
  "qudits_1": {
    "x_duration": 5E-08,
    "x_amplitude": 0.5,
    "qudit_freqs": 4920000000.0,
    "x_phase": 0.0,
    "x_post_phase": 0.0
  },
  "qudits_2": {
    "x_duration": 5E-08,
    "x_amplitude": 0.5,
    "qudit_freqs": 4930000000.0,
    "x_phase": 0.0,
    "x_post_phase": 0.0
  },
  "qudits_3": {
    "x_duration": 5E-08,
    "x_amplitude": 0.5,
    "qudit_freqs": 4940000000.0,
    "x_phase": 0.0,
    "x_post_phase": 0.0
  }
}



In [8]:
calset.import_values("calibration_values.qcs")

In [9]:

# Define the gate operation through a ZX Hamiltonian - the & operator represents
# the Kronecker product
cr_gate = qcs.ParametricGate([qcs.PAULIS.sigma_z & qcs.PAULIS.sigma_x], ["beta"])

angles = qcs.Array(name="beta", value=[0.3, 0.4], dtype=float)
cr_param_gate = qcs.ParameterizedGate(cr_gate, angles)

dur = qcs.Array("multi_qubit_duration", value=[50e-9, 60e-9], dtype=float)
amps = qcs.Array("multi_qubit_amplitudes", value=[1, 1], dtype=float)

# define the waveforms to replace the gate with

# play the control waveform with the frequency of the target qudits
cr_control_waveform = qcs.RFWaveform(
    dur, qcs.GaussianEnvelope(), amps * angles, qudit_frequencies[2:]
)
# play a compensating waveform on the control qudits with smaller amplitude
cr_target_waveform = qcs.RFWaveform(
    dur, qcs.GaussianEnvelope(), amps * angles * 0.2, qudit_frequencies[2:]
)

# add to calibration set
calset.add_cr_gate(
    cr_param_gate,
    pairs,
    "x",
    control_waveform=cr_control_waveform,
    target_waveform=cr_target_waveform,
    name="CR",
)

In [10]:
readout_drive_pulse = qcs.RFWaveform(
    300e-9, qcs.GaussianEnvelope(), 0.5, readout_frequencies
)

# add to the calibration set
calset.add_measurement(
    readout_drive_pulse,
    name="measure",
    readout_channels=channels,
    acquire_channels=readout_channels,
)

In [11]:
program = qcs.Program()

program.add_gate(qcs.GATES.x, qudits[0])
program.add_gate(qcs.GATES.x, qudits[1])

program.add_parametric_gate(cr_gate, angles[:1], (qudits[0], qudits[2]))
program.add_parametric_gate(cr_gate, angles[:1], (qudits[1], qudits[3]))

program.add_measurement(qudits)

program.draw()

In [12]:
compiled_program = qcs.LinkerPass(*calset.linkers.values()).apply(program)

compiled_program.draw()

In [13]:
calset.variable_list

[Array(name=x_duration, shape=(4,), dtype=float, unit=s),
 Array(name=x_amplitude, shape=(4,), dtype=float, unit=none),
 Array(name=qudit_freqs, shape=(4,), dtype=float, unit=Hz),
 Array(name=x_phase, shape=(4,), dtype=float, unit=rad),
 Array(name=x_post_phase, shape=(4,), dtype=float, unit=rad),
 Array(name=beta, shape=(2,), dtype=float, unit=none),
 Array(name=multi_qubit_duration, shape=(2,), dtype=float, unit=s),
 Array(name=multi_qubit_amplitudes, shape=(2,), dtype=float, unit=none),
 Array(name=CR_control_phase, shape=(2,), dtype=float, unit=rad),
 Array(name=CR_control_post_phase, shape=(2,), dtype=float, unit=rad),
 Array(name=CR_target_phase, shape=(2,), dtype=float, unit=rad),
 Array(name=CR_target_post_phase, shape=(2,), dtype=float, unit=rad),
 Array(name=measure_duration, shape=(4,), dtype=float, unit=s),
 Array(name=measure_amplitude, shape=(4,), dtype=float, unit=none),
 Array(name=readout_freqs, shape=(4,), dtype=float, unit=Hz),
 Array(name=measure_phase, shape=(4,), 